In [162]:
from torch.utils.data import DataLoader
import pandas as pd
import numpy as np
from torch.utils.data import Dataset
import os

In [234]:
forder= os.listdir('1월 데이터')

forder.sort()
# print(forder)

# exit()
weather_by_region = {}
for file in forder:
    csv = pd.read_csv('1월 데이터/' + file, encoding='CP949')
    csv = csv.drop(['지점명'], axis=1)
    groups = csv.groupby(csv.columns[0])
    for i in groups:
        if weather_by_region.get(i[0]) is not None:
            weather_by_region[i[0]].append(list(i))
        else:
            weather_by_region[i[0]] = list(i)

In [235]:
type(weather_by_region[310][1])

for i in weather_by_region:
    region_data=weather_by_region[i]
    concated_data = region_data[1]
    # print(type(concated_data))
    size = len(region_data)
    # print(concated_data)
    for j in range(2,size):
        # print(region_data[j])
        # print(type(region_data[j][1]))
        concated_data = pd.concat([concated_data, region_data[j][1]])
        
    weather_by_region[i]=concated_data.values

In [237]:
weather_by_region[310]

array([[310, '2022-01-01 00:01', -2.2, 0, 0.0, 0.0, 267.9, 0, 3.1, 0,
        1026.8, 0, 1028.6, 0, 21.1, 0],
       [310, '2022-01-01 00:02', -2.2, 0, 0.0, 0.0, 275.2, 0, 2.0, 0,
        1026.8, 0, 1028.6, 0, 20.6, 0],
       [310, '2022-01-01 00:03', -2.3, 0, 0.0, 0.0, 266.5, 0, 2.5, 0,
        1026.8, 0, 1028.6, 0, 21.2, 0],
       [310, '2022-01-01 00:04', -2.2, 0, 0.0, 0.0, 265.2, 0, 3.4, 0,
        1026.8, 0, 1028.6, 0, 20.7, 0],
       [310, '2022-01-01 00:05', -2.1, 0, 0.0, 0.0, 270.8, 0, 3.6, 0,
        1026.8, 0, 1028.6, 0, 20.5, 0],
       [310, '2022-01-01 00:06', -2.1, 0, 0.0, 0.0, 253.5, 0, 2.9, 0,
        1026.8, 0, 1028.6, 0, 20.2, 0],
       [310, '2022-01-01 00:07', -2.0, 0, 0.0, 0.0, 267.1, 0, 3.4, 0,
        1026.8, 0, 1028.6, 0, 20.1, 0],
       [310, '2022-01-01 00:08', -2.1, 0, 0.0, 0.0, 268.7, 0, 2.8, 0,
        1026.8, 0, 1028.6, 0, 20.3, 0],
       [310, '2022-01-01 00:09', -2.1, 0, 0.0, 0.0, 264.7, 0, 3.3, 0,
        1026.8, 0, 1028.6, 0, 20.7, 0],
       [31

In [238]:
powers = []
forder = os.listdir('2022_01_energy/2022_01')

forder=sorted(forder,key=lambda x:int(x.split('.')[0]))
# print(forder)

for file in forder:
    xlsx = pd.read_excel('2022_01_energy/2022_01/'+file, engine='openpyxl', skiprows=range(4))
    xlsx = xlsx.iloc[:-1, :]  #row remove
    powers.append(xlsx)

In [239]:
print(len(powers))

# print(powers[0].iloc[8][0])

31


In [185]:
import torch

class CustomDataset(Dataset):
    def __init__(self, weather, energy):
        self.weather = weather # 일자별 df 배열
        self.energy = energy # 에너지 리스트 일자 상관없음.
        # self.weather = pd.concat(self.weather, axis=0)
    
    def __len__(self):
        return len(self.energy)
    
    def __getitem__(self, idx):
        weather_data = []
        
        i = 0
        for region_data in self.weather[idx]:
            weather_data.append([])
            region_data['일시'] = pd.to_datetime(region_data['일시'])
            region_mean = region_data.resample('1H', on='일시').mean()
            index=0
            for _, row in region_mean.iterrows():
                if index == 23:
                    continue
                weather_data[i].append(row[2:])
                index+=1
            i+=1
        # weather_data = [[weather_data[j][i] for j in range(len(weather_data))] for i in range(len(weather_data[0]))]
        weather_tensor = torch.tensor(weather_data, dtype=torch.float32)
        weather_tensor = weather_tensor.permute(1, 0, 2)
        energy_data=[] 
        for i in range(23):
            energy_data.append(self.energy[idx])
        energy_tensor = torch.tensor(energy_data, dtype=torch.float32)
        
        return weather_tensor,energy_tensor

dataset = CustomDataset(weathers, powers)
dataloader = DataLoader(dataset, batch_size=10, shuffle=False)

TypeError: cannot concatenate object of type '<class 'list'>'; only Series and DataFrame objs are valid

In [183]:
import sys
# np.set_printoptions(threshold=sys.maxsize)

for data,result in dataloader:
    # print(np.array(data[0]))
    print(f'data : {data.shape} result : {result.shape}')

data : torch.Size([10, 23, 76, 14]) result : torch.Size([10, 23])
data : torch.Size([10, 23, 76, 14]) result : torch.Size([10, 23])
data : torch.Size([10, 23, 76, 14]) result : torch.Size([10, 23])


IndexError: list index out of range

In [ ]:
from torch import nn
from torch import optim


class predictModel(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(predictModel, self).__init__()
        self.dense = nn.Linear(76, 1)
        self.rnn = nn.RNN(input_size, hidden_size, batch_first=True)
        self.fc = nn.Linear(hidden_size, output_size)
        
    def forward(self,x):
        # print("size of x: ", x) # torch.Size([10, 23, 76, 14])
        x = x.permute(0,1,3,2) # x.shape: (10, 23, 14, 76)
        x = self.dense(x) # x.shape: (10, 23, 14, 1)
        x = x.squeeze(-1) # x.shape: (10, 23, 14)
        out, _ = self.rnn(x)  # out shape: (batch_size, seq_len, hidden_size)
        out = self.fc(out[:, -1, :])  # out shape: (batch_size, output_size)
        return out


In [ ]:
def train(model):
    criterion = nn.MSELoss()
    # 옵티마이저 정의
    optimizer = optim.SGD(model.parameters(), lr=0.01)

    for data, result in dataloader:
        optimizer.zero_grad()  # 경사 초기화
        # print(data.shape)

        outputs = model(data)  # 순전파
        print(f'outputs.shape : {outputs.shape} result.shape : {result.shape}')
        loss = criterion(outputs, result)  # 손실 계산
        loss.backward()  # 역전파
        optimizer.step()  # 파라미터 업데이트
        print(f'train loss: {loss.item():.4f}')
    

In [ ]:
epoch=100
model = predictModel(14, 128,23)

for i in range(epoch):
    train(model)

outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan


/home/user/anaconda3/lib/python3.9/site-packages/torch/autograd/__init__.py:173: UserWarning: CUDA initialization: Unexpected error from cudaGetDeviceCount(). Did you run some cuda functions before calling NumCudaDevices() that might have already set an error? Error 804: forward compatibility was attempted on non supported HW (Triggered internally at  /opt/conda/conda-bld/pytorch_1659484806139/work/c10/cuda/CUDAFunctions.cpp:109.)
  Variable._execution_engine.run_backward(  # Calls into the C++ engine to run the backward pass


outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([1, 23]) result.shape : torch.Size([1, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([1, 23]) result.shape : torch.Size([1, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([10, 23]) result.shape : torch.Size([10, 23])
train loss: nan
outputs.shape : torch.Size([1, 23]) result.shape : torch.Size([1, 23])
train loss: nan
outputs.shape : torch.Size(

KeyboardInterrupt: 